In [2]:
import os
import re
import json
import faiss
import warnings
import pandas as pd
import huggingface_hub

from openai import OpenAI

from langchain.schema import Document
from langchain_community.vectorstores.faiss import FAISS

from langchain.schema import Document
from langchain_openai import OpenAIEmbeddings
from langchain_upstage import UpstageEmbeddings
from langchain.retrievers import ContextualCompressionRetriever
from langchain_huggingface.embeddings import HuggingFaceEmbeddings
from langchain_community.docstore.in_memory import InMemoryDocstore
from langchain_community.cross_encoders import HuggingFaceCrossEncoder
from langchain.retrievers.document_compressors import CrossEncoderReranker


os.environ["TOKENIZERS_PARALLELISM"] = "false"
warnings.filterwarnings("ignore", category=FutureWarning)

from dotenv import load_dotenv
load_dotenv("../keys.env")

upstage_api_key = os.getenv("UPSTAGE_API_KEY")
os.environ['UPSTAGE_API_KEY'] = upstage_api_key

openai_api_key = os.getenv('OPENAI_API_KEY')
os.environ['OPENAI_API_KEY'] = openai_api_key

hf_token = os.getenv("HF_TOKEN")
huggingface_hub.login(hf_token)

The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: read).
Your token has been saved to /home/pervinco/.cache/huggingface/token
Login successful


In [3]:
client = OpenAI()
model = "gpt-4o"

In [4]:
def load_jsonl(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        return [json.loads(line) for line in f]

def load_document(path='../dataset/documents.jsonl'):
    raw_documents = load_jsonl(path)

    documents = []
    for doc in raw_documents:
        doc_id = doc['docid']
        content = doc['content']
        documents.append(Document(page_content=content, metadata={"docid": doc_id}))

    return documents

documents = load_document(path="../dataset/processed_documents.jsonl")

In [5]:
def clean_json_response(response):
    # 코드 블록(예: ```json, ```) 제거
    cleaned_response = re.sub(r'```(?:json)?', '', response).strip()
    return cleaned_response

In [12]:
def generate_keyword(document, model:str, client:OpenAI):
    prompt = (
        "당신은 주어진 문서를 읽고 이해하여 핵심을 파악하는 언어 전문가입니다. "
        "주어진 문서를 읽은 후에 문서와 관련성이 높은 질문을 세 가지 생성해야 합니다."
        "추가적으로 해당 문서가 어떤 분야에 해당하는지 하나의 단어로 구성된 도메인을 선정해야 합니다. "
        "반환하는 형식은 반드시 JSON 포맷이어야 하며, 모든 문자열은 쌍따옴표로 감싸야 합니다. "
        "형식은 다음과 같아야 합니다: "
        '{ "question1": "생성한 첫번째 질문", "question2" : "생성한 두번째 질문", "question3" : "생성한 세번째 질문", "domain" : "생성한 도메인"}. '
    )

    completion = client.chat.completions.create(
        model=model,
        messages=[
            {"role" : "system", "content" : prompt},
            {"role" : "user", "content" : document}
        ],
    )
    
    response = completion.choices[0].message.content
    response = clean_json_response(response)
    
    try:
        json_response = json.loads(response)
    except json.JSONDecodeError:
        return {"error": "Invalid JSON response", "response": response}
    
    return json_response

In [13]:
sample_doc = documents[0]
print(sample_doc.page_content)

result = generate_keyword(sample_doc.page_content, model, client)
print(result)

건강한 사람이 에너지 균형을 평형 상태로 유지하는 것은 중요합니다. 에너지 균형은 에너지 섭취와 에너지 소비의 수학적 동등성을 의미합니다. 일반적으로 건강한 사람은 1-2주의 기간 동안 에너지 균형을 달성합니다. 이 기간 동안에는 올바른 식단과 적절한 운동을 통해 에너지 섭취와 에너지 소비를 조절해야 합니다. 식단은 영양가 있는 식품을 포함하고, 적절한 칼로리를 섭취해야 합니다. 또한, 운동은 에너지 소비를 촉진시키고 근육을 강화시킵니다. 이렇게 에너지 균형을 유지하면 건강을 유지하고 비만이나 영양 실조와 같은 문제를 예방할 수 있습니다. 따라서 건강한 사람은 에너지 균형을 평형 상태로 유지하는 것이 중요하며, 이를 위해 1-2주의 기간 동안 식단과 운동을 조절해야 합니다.
{'question1': '에너지 균형이란 무엇을 의미하나요?', 'question2': '에너지 균형을 유지하기 위해 어떻게 식단과 운동을 조절할 수 있나요?', 'question3': '에너지 균형을 유지하면 어떤 건강상의 이점이 있나요?', 'domain': '건강'}


In [14]:
labeled_documents = []

for idx, doc in enumerate(documents):
    docid = doc.metadata.get('docid')
    content = doc.page_content
    print(f"{idx}\n{docid}\n{content}")

    result = generate_keyword(content, model, client)
    print(f"{result}\n") ## question, keyword
    
    if "quetion1" in result and 'question2' in result and 'question3' in result and 'domain' in result:
        doc.metadata["question1"] = result["question1"]
        doc.metadata["question2"] = result["question2"]
        doc.metadata["question3"] = result["question3"]
        doc.metadata["domain"] = result["domain"]
    else:
        doc.metadata["question1"] = result["question1"]
        doc.metadata["question2"] = result["question2"]
        doc.metadata["question3"] = result["question3"]
        doc.metadata["domain"] = result["domain"]
    
    labeled_documents.append({
        "docid": doc.metadata["docid"],
        "content": doc.page_content,
        "domain" : doc.metadata['domain'],
        "question1" : doc.metadata['question1'],
        "question2" : doc.metadata['question2'],
        "question3" : doc.metadata['question3'],
    })

with open("../dataset/processed_documents_queries.jsonl", 'w', encoding='utf-8') as f:
    for entry in labeled_documents:
        json.dump(entry, f, ensure_ascii=False)
        f.write('\n')

0
42508ee0-c543-4338-878e-d98c6babee66
건강한 사람이 에너지 균형을 평형 상태로 유지하는 것은 중요합니다. 에너지 균형은 에너지 섭취와 에너지 소비의 수학적 동등성을 의미합니다. 일반적으로 건강한 사람은 1-2주의 기간 동안 에너지 균형을 달성합니다. 이 기간 동안에는 올바른 식단과 적절한 운동을 통해 에너지 섭취와 에너지 소비를 조절해야 합니다. 식단은 영양가 있는 식품을 포함하고, 적절한 칼로리를 섭취해야 합니다. 또한, 운동은 에너지 소비를 촉진시키고 근육을 강화시킵니다. 이렇게 에너지 균형을 유지하면 건강을 유지하고 비만이나 영양 실조와 같은 문제를 예방할 수 있습니다. 따라서 건강한 사람은 에너지 균형을 평형 상태로 유지하는 것이 중요하며, 이를 위해 1-2주의 기간 동안 식단과 운동을 조절해야 합니다.
{'question1': '에너지 균형을 달성하기 위해 어떻게 식단을 조절해야 하나요?', 'question2': '운동이 에너지 균형에 미치는 영향은 무엇인가요?', 'question3': '에너지 균형을 유지하면 어떤 건강상의 이점을 얻을 수 있나요?', 'domain': 'Nutrition'}

1
4a437e7f-16c1-4c62-96b9-f173d44f4339
수소, 산소, 질소 가스의 혼합물에서 평균 속도가 가장 빠른 분자는 수소입니다. 수소 분자는 가장 가볍고 작은 원자로 구성되어 있기 때문에 다른 분자들보다 더 빠르게 움직입니다. 이러한 이유로 수소 분자는 주어진 온도에서 가장 빠른 평균 속도를 가지고 있습니다. 수소 분자는 화학 반응에서도 활발하게 참여하며, 수소 연료로도 널리 사용됩니다. 따라서 수소 분자는 주어진 온도에서 평균 속도가 가장 빠른 분자입니다.
{'question1': '수소 분자가 평균 속도가 가장 빠른 이유는 무엇인가요?', 'question2': '수소가 화학 반응에서 중요한 역할을 하는 이유는 무엇인가요?', 'question3': '수소 연료의 장점은 무엇인가요?', 'domain